In [1]:

import requests
from config import geoapify_key 
import csv
import pandas as pd
import pprint
import json
import time 



In [2]:
# get the data from the json file
json_path = "./Resources/IMDB_API_adventure100_location.json"
df = pd.read_json(json_path)
# remove the duplicate rows by location_name
df = df.drop_duplicates(subset=['location_name'], keep='first')

# create a new list to store the data
location_list = []

In [7]:
# loop through the rows and get the location data
for index, row in df.iterrows():
    time.sleep(1)
    text = row["location_name"]
    url = "https://api.geoapify.com/v1/geocode/autocomplete?text="+text+"&format=json&apiKey="+geoapify_key
          
    response = requests.get(url)
       
    pprint.pprint(response.json())
    locationinfo = {}
    locationinfo["location_name"] = row["location_name"]
    if len(response.json()['results'])==0:
        print("No location found")
        print(text)
        # remove everything berfore the first comma
        text = text.replace("UK","United Kingdom")
        if " - " in text:
            text = text.split(" - ",1)[1]
        elif "," in text:
            text = text.split(",",1)[1]
        
        url = "https://api.geoapify.com/v1/geocode/autocomplete?text="+text+"&format=json&apiKey="+geoapify_key
        response = requests.get(url)
        if len(response.json()['results'])==0:
            print("No location found")
            print(text)
            locationinfo["lat"] = "N/A"
            locationinfo["lon"] = "N/A"
       
        else :
            locationinfo["lat"] = response.json()["results"][0]["lat"]
            locationinfo["lon"] = response.json()["results"][0]["lon"]
    
    else:
        locationinfo["lat"] = response.json()["results"][0]["lat"]
        locationinfo["lon"] = response.json()["results"][0]["lon"]
# add to list of dictionaries
    location_list.append(locationinfo)




{'query': {'parsed': {'city': 'bangkok',
                      'country': 'thailand',
                      'expected_type': 'city'},
           'text': 'Bangkok, Thailand'},
 'results': [{'address_line1': 'Bangkok',
              'address_line2': 'Bangkok, Bangkok 10200, Thailand',
              'bbox': {'lat1': 13.5924938,
                       'lat2': 13.9124938,
                       'lon1': 100.3335089,
                       'lon2': 100.6535089},
              'category': 'populated_place',
              'city': 'Bangkok',
              'country': 'Thailand',
              'country_code': 'th',
              'datasource': {'attribution': '© OpenStreetMap contributors',
                             'license': 'Open Database License',
                             'sourcename': 'openstreetmap',
                             'url': 'https://www.openstreetmap.org/copyright'},
              'formatted': 'Bangkok, Bangkok 10200, Thailand',
              'lat': 13.7524938,
             

In [ ]:
# create a new dataframe
location_df = pd.DataFrame(location_list)
location_df.head()
# reorder the columns
location_df = location_df[["location_name","lat","lon"]]
# save the dataframe to csv file
location_df.to_csv("./Resources/IMDB_API_adventure100_location_geoapify.csv", index=False)
location_df.to_json("./Resources/IMDB_API_adventure100_location_geoapify.json", orient="records")
